In [1]:
import geopandas as gpd
import pandas as pd
import osmnx as ox
import matplotlib.pyplot as plt
import os
import folium
import alphashape
import numpy as np
from tqdm.notebook import tqdm
import networkx as nx
%matplotlib inline

In [255]:
class Network:
    def __init__(self, crs = 32618):
        self.crs = crs
        self.n_pot = None
        self.n_pot_nodes = None
        self.n_pot_edges = None
        self.n_ex = None
        self.n_ex_nodes = None
        self.n_ex_edges = None
        self.trips = None
        self.map_pot = None
        self.map_ex = None
        self.map_routes = None
        self.trips = None
        self.trips_within = None
        self.sample = None
        self.boundaries = None
        self.routes = []
        self.all_routes_edges = None
        self.routes_summary = None
        self.links = None
        
    def load_n_pot(self,path):
        self.n_pot = ox.io.load_graphml(path)
        self.n_pot = ox.project_graph(self.n_pot)
        # self.n_pot = ox.consolidate_intersections(G_proj, rebuild_graph=True, tolerance=10, dead_ends=False)
        self.n_pot_nodes,self.n_pot_edges = ox.graph_to_gdfs(self.n_pot)
        
    def filter_n_pot(self):
        self.n_pot_edges[self.n_pot_eges.highway.isin(['residential','primary','secondary','tertiary','tertiary_link'])]
        self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)

    def plot_n_pot(self, nodes = False):
        if self.n_pot == None:
            print('No potential network loaded')
        else:
            self.map_pot = self.n_pot_edges.explore(color = 'black')
            if nodes:
                self.n_pot_nodes.explore(m = self.map_pot)
            display(self.map_pot)

    def load_n_ex(self,path):
        self.n_ex = ox.io.load_graphml(path)
        self.n_ex = ox.project_graph(self.n_ex)
        # self.n_ex = ox.consolidate_intersections(G_proj, rebuild_graph=True, tolerance=10, dead_ends=False)
        self.n_ex_nodes,self.n_ex_edges = ox.graph_to_gdfs(self.n_ex)

    def filter_n_ex(self,highway_type = 'cycleway'):
        self.n_ex_edges = self.n_ex_edges[self.n_ex_edges.highway == highway_type]
        self.n_ex = ox.graph_from_gdfs(self.n_ex_nodes,self.n_ex_edges)

    def plot_n_ex(self, nodes = False):
        if self.n_ex == None:
            print('No existing network loaded')
        else:
            self.map_ex = self.n_ex_edges.explore(color = 'black')
            if nodes:
                self.n_ex_nodes.explore(m = self.map_ex)
            display(self.map_ex)

    def load_trips(self, path, cols = ['ipere','feuillet','rang','xorig','yorig','xdest','ydest','mode','potVelo','fexpPotVelo']):
        self.trips = pd.read_csv(path)
        self.trips = self.trips[self.trips.potVelo == 1]
        self.trips = self.trips[cols]
        self.trips = gpd.GeoDataFrame(self.trips, geometry=gpd.points_from_xy(self.trips.xorig, self.trips.yorig), crs=32188)
        self.trips = self.trips.rename(columns = {'geometry': 'orig'})
        self.trips = self.trips.assign(dest = gpd.points_from_xy(self.trips.xdest, self.trips.ydest,crs=32188))
        self.trips = self.trips.set_geometry('orig')
        self.trips = self.trips.to_crs(self.crs)
        self.boundaries = gpd.GeoDataFrame({'name':['region']},geometry = gpd.GeoSeries(self.n_pot_nodes.geometry.union_all()).concave_hull(0.3)
                                           , crs = self.crs)
        
        self.trips = self.trips.to_crs(self.crs)
        self.trips_within = gpd.sjoin(self.trips, self.boundaries, how='inner', predicate='within')[list(self.trips.columns)]
        self.trips_within = self.trips_within.set_geometry('dest')
        self.trips_within = self.trips_within.to_crs(self.crs)
        self.trips_within = gpd.sjoin(self.trips_within, self.boundaries, how='inner', predicate='within')[list(self.trips.columns)]

    def compute_routes(self, network, sample_size = None, spec_route = None, weight = 'gencost'):
        if sample_size is None:
            sample_size = len(self.trips_within)
            self.sample = self.trips_within.sample(sample_size)
        else:
            self.sample = pd.concat([self.sample,self.trips_within.sample(sample_size)])

        if spec_route is not None:
            self.sample = self.trips_within[self.trips_within.ipere == spec_route]
        network = ox.projection.project_graph(network, to_crs = self.crs)
        o_nodes,o_dists = ox.nearest_nodes(network,self.sample.orig.x.values,self.sample.orig.y.values, return_dist=True)
        d_nodes,d_dists = ox.nearest_nodes(network,self.sample.dest.x.values,self.sample.dest.y.values, return_dist=True)
        routes = ox.shortest_path(network, o_nodes, d_nodes, weight=weight)
        self.routes+=routes

    def get_routes_edges(self,network):
        routes_edges = []
        unsolved = []
        static = []
        
        for i in tqdm(range(len(self.routes))):
            if self.routes[i] is not None:
                if len(self.routes[i])>1:
                    edges = ox.routing.route_to_gdf(network,self.routes[i])
                    edges = edges.assign(route_number = i)
                    routes_edges.append(edges)
            elif self.routes[i] is None:
                unsolved.append(i)
            else:
                static.append(self.routes[i])
        print(str(len(unsolved))+' trips unsolved')
        print(str(len(static))+' static trips')
        
        self.all_routes_edges = pd.concat(routes_edges)

    def plot_routes(self,network):

        if self.all_routes_edges is None:
            self.get_routes_edges(network)
        
        self.routes_summary = self.all_routes_edges[['length','gencost','route_number']].groupby(['route_number']).sum()

        self.sample = self.sample.set_geometry('orig')
        self.map_routes = self.sample.explore(color='blue', name='orig')
        self.sample = self.sample.set_geometry('dest')
        map2 = self.sample.explore(color='red', name='dest', m=self.map_routes)
        map3 = self.boundaries.explore(m = self.map_routes, name = 'boundaries', fill = False)
        map4 = self.n_ex_edges.explore(color='black', name='existing', m=self.map_routes)
        map5 = self.n_pot_edges.explore(color='black', name='potential', m=self.map_routes)
        map8 = self.all_routes_edges.explore(column = 'route_number',cmap = 'gist_rainbow', name = 'routes', m = self.map_routes, legend = False)
        folium.LayerControl().add_to(self.map_routes)
        display(self.map_routes)

    def weight_network(self,cycleway_reduc_factor=0.9):
        self.n_pot_edges['gencost'] = self.n_pot_edges["length"] * self.n_pot_edges["highway"].apply(lambda x: cycleway_reduc_factor if x == "cycleway" else 1)
        self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)


    def run_algo(self,n_iter_max = np.inf, budget = 10000):
        if self.all_routes_edges is None:
            self.get_routes_edges(self.n_pot)
            
        links = self.all_routes_edges[self.all_routes_edges.highway !='cycleway'].drop_duplicates(['length'])
        flows = self.all_routes_edges[self.all_routes_edges.highway !='cycleway'].groupby(by = ['length'], as_index = False).size()['size']
        links['flow'] = flows.values
        links['flux'] = flows.values*links.length
        i = 0
        while sum(links.length)>budget:
            if i>=n_iter_max:
                print('max iter reached')
                break
            minflux = min(links['flux'])
            links = links.drop(links[links.flux == minflux].index)
        self.links = links

In [256]:
n = Network()
ex = 'Data/Reseaux/ns_EX_Villeray-Saint-Michel-Parc-Extension.graphml'
pot = 'Data/Reseaux/ns_POT_Villeray-Saint-Michel-Parc-Extension.graphml'
trips = 'Data/od18_extraqit_20250123/od18_extraqit_20250123.csv'

In [257]:
n.load_n_pot(pot)
n.load_n_ex(ex)
n.load_trips(trips)

In [258]:
n.trips = n.trips[n.trips['mode']!='TC']

In [259]:
n.weight_network(cycleway_reduc_factor=0.8)

In [260]:
%%time
n.routes = []
n.sample = None
n.all_routes_edges = None
n.compute_routes(n.n_pot, sample_size = 10,weight='gencost')

CPU times: total: 406 ms
Wall time: 383 ms


In [261]:
n.plot_routes(n.n_pot)

  0%|          | 0/10 [00:00<?, ?it/s]

0 trips unsolved
0 static trips


In [262]:
n.run_algo()

In [270]:
new_edges = pd.concat([n.links,n.n_ex_edges])
new_edges.explore(columns = ['highway'], cmap = 'Set1')

In [271]:
new_edges

osmid  \
u           v           key                                                      
437851665   437850049   0                                            165090581   
437850049   437848506   0                                            165090581   
437848506   8557781955  0                                           1211711553   
437850054   516591914   0    [977958080, 1154398114, 1252393067, 554029774,...   
516591914   2091857134  0                   [1154398120, 20231834, 1154398118]   
...                                                                        ...   
9546320891  9546320913  0                                           1036167901   
9546320913  9546320891  0                                           1036167901   
10736121278 516591914   0                                           1252393032   
10899407591 11564332394 0                                           1244083334   
12285953157 12285953158 0                                           1327926699   

                               highway   lanes maxspeed                  name  \
u           v           key                                                     
437851665   437850049   0     tertiary       2       30        Avenue Querbes   
437850049   437848506   0     tertiary       2       30        Avenue Querbes   
437848506   8557781955  0     tertiary       2       30        Avenue Querbes   
437850054   516591914   0    secondary       2       50       Rue Jarry Ouest   
516591914   2091857134  0    secondary  [3, 2]       50       Rue Jarry Ouest   
...                                ...     ...      ...                   ...   
9546320891  9546320913  0     cycleway     NaN      NaN                   NaN   
9546320913  9546320891  0     cycleway     NaN      NaN                   NaN   
10736121278 516591914   0     cycleway     NaN      NaN       Rue Jarry Ouest   
10899407591 11564332394 0     cycleway     NaN      NaN  Rue Jean-Talon Ouest   
12285953157 12285953158 0     cycleway     NaN      NaN    Avenue de Lorimier   

                             oneway reversed      length  \
u           v           key                                
437851665   437850049   0     False    False  320.413117   
437850049   437848506   0     False    False  262.910590   
437848506   8557781955  0     False    False  222.481452   
437850054   516591914   0      True    False  274.339948   
516591914   2091857134  0      True    False  101.369349   
...                             ...      ...         ...   
9546320891  9546320913  0     False    False    6.094691   
9546320913  9546320891  0     False     True    6.094691   
10736121278 516591914   0      True    False    9.217631   
10899407591 11564332394 0      True    False    9.252734   
12285953157 12285953158 0      True    False   60.800637   

                                                                      geometry  \
u           v           key                                                      
437851665   437850049   0    LINESTRING (607347.925 5042643.297, 607339.799...   
437850049   437848506   0    LINESTRING (607049.322 5042761.277, 607041.189...   
437848506   8557781955  0    LINESTRING (606804.215 5042857.879, 606796.446...   
437850054   516591914   0    LINESTRING (606557.409 5042955.718, 606560.328...   
516591914   2091857134  0    LINESTRING (606659.782 5043209.422, 606683.355...   
...                                                                        ...   
9546320891  9546320913  0    LINESTRING (608382.432 5045568.997, 608385.7 5...   
9546320913  9546320891  0    LINESTRING (608385.7 5045574.143, 608382.432 5...   
10736121278 516591914   0    LINESTRING (606664.339 5043201.41, 606659.782 ...   
10899407591 11564332394 0    LINESTRING (607569.074 5042783.566, 607569.741...   
12285953157 12285953158 0    LINESTRING (605874.64 5046920.707, 605925.238 ...   

                                gencost access tunnel  route_number service  \
u           v           k

In [58]:
n.trips_within[n.trips_within.ipere==28163]
o_nodes,o_dists = ox.nearest_nodes(n.n_pot,n.sample.orig.x.values,n.sample.orig.y.values, return_dist=True)
d_nodes,d_dists = ox.nearest_nodes(n.n_pot,n.sample.dest.x.values,n.sample.dest.y.values, return_dist=True)

In [79]:
routes = ox.routing.k_shortest_paths(n.n_pot,o_nodes[0],d_nodes[0],k = 30)

In [117]:
G_simple = ox.convert.to_digraph(n.n_pot)

In [8]:
ox.routing.route_to_gdf(n.n_pot,nx.dijkstra_path(G_simple, o_nodes[0], d_nodes[0], weight="length")).explore()

NameError: name 'G_simple' is not defined

In [129]:
n.routes_summary

length      gencost
route_number                          
0             3163.701117  3163.701117
1             2594.774454  2594.774454